In [28]:
import numpy as np
import torch
import torch.nn as nn
import torch.optim as optim
import plotly.graph_objects as go

In [29]:
np.random.seed(2)
X = np.random.uniform(-10, 10, 150)
epsilon = np.random.normal(0, 1, 150)
y = 2 * X**2 + 3 * X + 1 + epsilon

In [30]:
# Convert the data to PyTorch tensors
X_tensor = torch.tensor(X, dtype=torch.float32).view(-1, 1)  # shape: (100, 1)
y_tensor = torch.tensor(y, dtype=torch.float32).view(-1, 1)  # shape: (100, 1)

In [31]:
# Define the Linear Regression model (for comparison)
class LinearRegressionModel(nn.Module):
    def __init__(self):
        super(LinearRegressionModel, self).__init__()
        self.linear = nn.Linear(1, 1)  # One feature to one output

    def forward(self, x):
        return self.linear(x)
    
linear_model = LinearRegressionModel()
linear_model_with_l2 = LinearRegressionModel()

In [32]:
class PolynomialRegressionModel(nn.Module):
    def __init__(self, degree):
        super(PolynomialRegressionModel, self).__init__()
        self.degree = degree
        self.poly = nn.Linear(degree + 1, 1)

    def forward(self, x):
        x_poly = torch.cat([x**i for i in range(self.degree + 1)], dim=1)
        return self.poly(x_poly)

poly_model = PolynomialRegressionModel(10)
poly_model_with_l2 = PolynomialRegressionModel(10)

In [33]:
# Train the models and track their losses
def train_model(model, X_tensor, y_tensor, num_epochs=1000, learning_rate=0.01, weight_decay=0.0):
    criterion = nn.MSELoss()
    # L2 regularyzation is made by add weight_decay for SGD
    optimizer = optim.SGD(model.parameters(), lr=learning_rate, weight_decay=weight_decay)
    
    loss_values = []

    for _ in range(num_epochs):
        # Forward pass: Compute predicted y by passing X to the model
        y_pred = model(X_tensor)
        loss = criterion(y_pred, y_tensor)
        optimizer.zero_grad()  # Zero the gradients before the backward pass
        loss.backward()  # Backpropagation
        optimizer.step()
        loss_values.append(loss.item())

    print(loss_values[-1])
    return loss_values

In [34]:
# Train models
linear_loss = train_model(linear_model, X_tensor, y_tensor)
poly_loss = train_model(poly_model, X_tensor, y_tensor)

linear_loss_with_l2 = train_model(linear_model, X_tensor, y_tensor, weight_decay=0.001)
poly_loss_with_l2 = train_model(poly_model, X_tensor, y_tensor, weight_decay=0.001)

3336.6767578125
nan
3336.677490234375
nan


In [35]:
# Visualize the training loss for both models using Plotly
fig = go.Figure()

# Add traces for both models
fig.add_trace(go.Scatter(x=np.arange(len(linear_loss)), y=linear_loss, mode='lines', name='Linear Regression'))
fig.add_trace(go.Scatter(x=np.arange(len(poly_loss)), y=poly_loss, mode='lines', name='Polynomial Regression (degree 10)'))
fig.add_trace(go.Scatter(x=np.arange(len(linear_loss_with_l2)), y=linear_loss_with_l2, mode='lines', name='Linear Regression with L2'))
fig.add_trace(go.Scatter(x=np.arange(len(poly_loss_with_l2)), y=poly_loss_with_l2, mode='lines', name='Polynomial Regression with L2 (degree 10)'))

# Customize the layout
fig.update_layout(
    title="Training Loss for Linear and Polynomial Regression Models",
    xaxis=dict(title="Epochs"),
    yaxis=dict(title="Loss (MSE)"),
    showlegend=True
)

# Show the plot
fig.show()

# 8. Output the learned parameters for both models
print("Linear Regression Model Parameters:")
for param in linear_model.parameters():
    print(param)

print("\nPolynomial Regression Model Parameters:")
for param in poly_model.parameters():
    print(param)

print("\nLinear Regression Model with L2 Parameters:")
for param in linear_model_with_l2.parameters():
    print(param)

print("\nPolynomial Regression Model with L2 Parameters:")
for param in poly_model_with_l2.parameters():
    print(param)

Linear Regression Model Parameters:
Parameter containing:
tensor([[1.8834]], requires_grad=True)
Parameter containing:
tensor([59.4863], requires_grad=True)

Polynomial Regression Model Parameters:
Parameter containing:
tensor([[nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan]],
       requires_grad=True)
Parameter containing:
tensor([nan], requires_grad=True)

Linear Regression Model with L2 Parameters:
Parameter containing:
tensor([[0.1039]], requires_grad=True)
Parameter containing:
tensor([-0.5172], requires_grad=True)

Polynomial Regression Model with L2 Parameters:
Parameter containing:
tensor([[-0.0715, -0.3007, -0.1260, -0.0576,  0.2413,  0.0898,  0.1677, -0.0800,
         -0.2616, -0.0142,  0.0862]], requires_grad=True)
Parameter containing:
tensor([0.1543], requires_grad=True)


In [36]:
# Plot the results using Plotly
X_space = torch.arange(-10, 10, 0.001, dtype=torch.float32).view(-1, 1)

predicted_linear = linear_model(X_space).detach().numpy()
predicted_poly = poly_model(X_space).detach().numpy()
predicted_linear_with_l2 = linear_model_with_l2(X_space).detach().numpy()
predicted_poly_with_l2 = poly_model_with_l2(X_space).detach().numpy()

scatter = go.Scatter(x=X, y=y, mode='markers', name='True data')
linear_line = go.Scatter(x=X_space.numpy().flatten(), y=predicted_linear.flatten(), mode='lines', name='Linear model', line=dict(color='green'))
poly_line = go.Scatter(x=X_space.numpy().flatten(), y=predicted_poly.flatten(), mode='lines', name='Poly model', line=dict(color='red'))
linear_line_with_l2 = go.Scatter(x=X_space.numpy().flatten(), y=predicted_linear_with_l2.flatten(), mode='lines', name='Linear model with L2', line=dict(color='green'))
poly_line_with_l2 = go.Scatter(x=X_space.numpy().flatten(), y=predicted_poly_with_l2.flatten(), mode='lines', name='Poly model with L2', line=dict(color='red'))

layout = go.Layout(
    title="Linear and Poly Regression Fit Compare",
    xaxis=dict(title="X"),
    yaxis=dict(title="y"),
    showlegend=True
)

fig = go.Figure(data=[scatter, linear_line, poly_line, linear_line_with_l2, poly_line_with_l2], layout=layout)
fig.show()